# DQN from scratch

In [1]:
from dataclasses import dataclass, replace
from functools import cache
import numpy as np
import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import torch
from tqdm.notebook import tqdm, trange
from typing import List

## Architecture

In [2]:
@dataclass(frozen=True)
class Observation:
    cash_balance: float
    asset_balance: float
    best_ask: float
    best_bid: float

    @property
    def array(self):
        return np.array(
            [self.cash_balance, self.asset_balance, self.best_ask, self.best_bid],
            dtype=np.float32,
        )
    
    @property
    def batch(self):
        return ObservationBatch([self])

    @property
    def total_balance(self):
        return self.cash_balance + self.asset_balance


@dataclass(frozen=True)
class ObservationBatch:
    observations: List[Observation]

    @property
    def tensor(self):
        return torch.tensor(
            np.stack([observation.array for observation in self.observations])
        )


@dataclass(frozen=True)
class Action:
    ask: float
    bid: float

    @property
    def array(self):
        return np.array([self.ask, self.bid], dtype=np.float32)
    
    @property
    def batch(self):
        return ActionBatch([self])


@dataclass(frozen=True)
class ActionBatch:
    actions: List[Action]

    @property
    def tensor(self):
        return torch.tensor(np.stack([action.array for action in self.actions]))


@dataclass(frozen=True)
class Experience:
    old_observation: Observation
    action: Action
    reward: float
    new_observation: Observation


In [3]:
class Critic(torch.nn.Module):
    def __init__(self):
        super().__init__()
        self.network = torch.nn.Sequential(
            torch.nn.Linear(6, 256),
            torch.nn.LeakyReLU(),
            torch.nn.Linear(256, 1),
        )

    def forward(self, tensor):
        return self.network(tensor)

    def evaluate(
        self, observations: ObservationBatch, actions: ActionBatch
    ) -> torch.Tensor:
        return self(torch.cat([observations.tensor, actions.tensor], axis=1)).squeeze(1)


@dataclass(frozen=False)
class Agent:
    critic: Critic
    target_critic: Critic
    num_tried_actions: int
    random_action_probability: float
    discount: float

    def act(self, observation: Observation) -> Action:
        if np.random.uniform() < self.random_action_probability:
            return self.random_action()
        return self.best_action(observation, critic=self.critic)

    def best_action(self, observation: Observation, critic: Critic) -> Action:
        random_actions = [self.random_action() for _ in range(self.num_tried_actions)]
        evaluations = critic.evaluate(
            ObservationBatch([observation] * self.num_tried_actions),
            ActionBatch(random_actions),
        )
        best_index = torch.argmax(evaluations, dim=0).item()
        return random_actions[best_index]

    @classmethod
    def random_action(cls) -> Action:
        random_price = lambda: np.random.uniform(0, 2)
        return Action(ask=random_price(), bid=random_price())

    def optimal(self, num_tried_actions=64):
        return replace(
            self, num_tried_actions=num_tried_actions, random_action_probability=0
        )


## Problem formulation

In [4]:
def sample_observation(cash_balance: float, asset_balance: float):
    mid_price = np.random.uniform(0.5, 1.5)
    spread = np.random.uniform(0.1, 0.3)
    return Observation(
        cash_balance=cash_balance,
        asset_balance=asset_balance,
        best_ask=mid_price + spread / 2,
        best_bid=mid_price - spread / 2,
    )

In [5]:
def mock_experience(agent: Agent, reward_offset: float) -> Experience:
    old_observation = sample_observation(cash_balance=1, asset_balance=1)
    
    action = agent.act(old_observation)
    new_cash_balance = old_observation.cash_balance
    new_asset_balance = old_observation.asset_balance
    
    if action.ask <= old_observation.best_bid:
        sold_assets = min(new_asset_balance, 1)
        new_cash_balance += action.ask * sold_assets
        new_asset_balance -= sold_assets
    if action.bid >= old_observation.best_ask:
        bought_assets = min(new_cash_balance / action.bid, 1)
        new_cash_balance -= action.bid * bought_assets
        new_asset_balance += bought_assets
    
    new_observation = sample_observation(cash_balance=new_cash_balance, asset_balance=new_asset_balance)
    return Experience(
        old_observation=old_observation,
        action=action,
        reward=new_observation.total_balance - old_observation.total_balance + reward_offset,
        new_observation=new_observation,
    )


## Training

In [6]:
@dataclass(frozen=True)
class Experiment:
    agent: Agent
    experiences: List[Experience]
    td_errors: List[float]
    biases: List[float]
    bias_grads: List[float]

    @classmethod
    def train(
        cls,
        learning_rate,
        num_tried_actions,
        num_steps,
        steps_per_target_update,
        reward_offset: float,
    ):
        agent = Agent(
            critic=Critic(),
            target_critic=Critic(),
            num_tried_actions=num_tried_actions,
            random_action_probability=None,  # gets set dynamically
            discount=0.99,
        )
        optimizer = torch.optim.Adam(agent.critic.parameters(), lr=learning_rate)
        experiences = []
        td_errors = []
        biases = []
        bias_grads = []
        for step_idx in trange(num_steps, desc="Training"):
            if step_idx % steps_per_target_update == 0:
                agent.target_critic.load_state_dict(agent.critic.state_dict())

            agent.random_action_probability = 1 / (step_idx + 1)
            experience = mock_experience(agent, reward_offset=reward_offset)
            experiences.append(experience)
            best_next_action = agent.best_action(
                experience.new_observation, critic=agent.target_critic
            )
            new_evaluation = agent.target_critic.evaluate(
                experience.new_observation.batch, best_next_action.batch
            )
            td_error = (
                experience.reward
                + agent.discount * new_evaluation.detach()
                - agent.critic.evaluate(
                    experience.old_observation.batch, experience.action.batch
                )
            )
            td_errors.append(td_error.item())

            critic_loss = td_error ** 2
            optimizer.zero_grad()
            critic_loss.backward()
            optimizer.step()
            biases.append(agent.critic.network[-1].bias.item())
            bias_grads.append(agent.critic.network[-1].bias.grad.item())

        return cls(
            agent=agent,
            experiences=experiences,
            td_errors=td_errors,
            biases=biases,
            bias_grads=bias_grads,
        )


base_experiment = Experiment.train(
    learning_rate=1e-4,
    num_tried_actions=64,
    num_steps=50_000,
    steps_per_target_update=5_000,
    reward_offset=0,
)
offset_experiment = Experiment.train(
    learning_rate=1e-4,
    num_tried_actions=64,
    num_steps=50_000,
    steps_per_target_update=5_000,
    reward_offset=2,
)
fast_offset_experiment = Experiment.train(
    learning_rate=1e-4,
    num_tried_actions=64,
    num_steps=50_000,
    steps_per_target_update=1_000,
    reward_offset=2,
)

Training:   0%|          | 0/50000 [00:00<?, ?it/s]

Training:   0%|          | 0/50000 [00:00<?, ?it/s]

Training:   0%|          | 0/50000 [00:00<?, ?it/s]

In [14]:
def theoretical_bound(start_value: float, num_updates: int):
    if num_updates == 0:
        return start_value
    old_bound = theoretical_bound(start_value, num_updates=num_updates - 1)
    discount = offset_experiment.agent.discount
    return old_bound * discount + (2 - old_bound) * (1 - discount)


go.Figure(
    layout=dict(
        xaxis_title="Training step",
        yaxis_title="Bias",
    ),
    data=[
        go.Scatter(name=f"Base experiment", y=base_experiment.biases),
        go.Scatter(name=f"Experiment with offset", y=offset_experiment.biases),
        go.Scatter(
            name="Theoretical bound with offset",
            y=[
                theoretical_bound(offset_experiment.biases[5_000], step // 5_000)
                for step in range(len(offset_experiment.biases))
            ],
        ),
        go.Scatter(
            name=f"Experiment with offset, frequent target updates",
            y=fast_offset_experiment.biases,
        ),
        go.Scatter(
            name="Theoretical bound, frequent target updates",
            y=[
                theoretical_bound(fast_offset_experiment.biases[1_000], step // 1_000)
                for step in range(len(fast_offset_experiment.biases))
            ],
        ),
    ],
)


It's hard to learn the bias because the target network is updated relatively rarely - and each update can only get us so much closer to the target value.